In [56]:
import pandas as pd


In [69]:
path_families = 'data/mehra/Annotation_of_rnd_families.csv'
path_annotation = 'data/mehra/repeat_co-ordinates_S_tuberosum.csv'
path_annotation_new = 'data/mehra/repeats.csv'
path_all = 'data/mehra/all.gff'
path_res = 'data/mehra/repeats_filtered.csv'
path_gff_genome = "data/mehra/Stuberosum_genome.gff3"


In [58]:
df_families = pd.read_csv(path_families, sep='\t',comment='#')
print(len(df_families.index))
df_families.head(2)

1243


Repeat Family Annotation           Annotation method
0  rnd-1_family-0  LTR/Gypsy  RepeatMasker_library_match
1  rnd-1_family-1  LTR/Gypsy           RepeatProteinMask

In [59]:
df_ann = pd.read_csv(path_annotation, sep='\t')
print(len(df_ann.index))
df_ann.head(2)

1061377


Repeat family  Chromosome    Start      End Strand
0  rnd-1_family-0           0  1053337  1054816      +
1  rnd-1_family-0           0  1060000  1060892      +

In [61]:
df_ann['Chromosome'] = df_ann['Chromosome'].apply(str)
df_ann['Chromosome'] = 'chr' + df_ann['Chromosome'].str.zfill(2)
df_ann.to_csv(path_annotation_new, index=None, sep='\t')

In [62]:
# filter low compexity or simple repeat
filter_out = ['Simple_repeat','Low_complexity','Simple_and_Low_complexity','rRNA','snRNA']
df_families_te = df_families[~df_families.Annotation.isin(filter_out)]
print(len(df_families_te.index))
df_families_te.head(2)

1063


Repeat Family Annotation           Annotation method
0  rnd-1_family-0  LTR/Gypsy  RepeatMasker_library_match
1  rnd-1_family-1  LTR/Gypsy           RepeatProteinMask

In [63]:
list_families = df_families_te['Repeat Family'].tolist()
df_ann_te = df_ann[df_ann['Repeat family'].isin(list_families)]
print(len(df_ann_te.index))
df_ann_te.head(2)

629713


Repeat family Chromosome    Start      End Strand
0  rnd-1_family-0      chr00  1053337  1054816      +
1  rnd-1_family-0      chr00  1060000  1060892      +

In [64]:
df_ann_te.to_csv(path_res, sep='\t', index=None)
path_res

In [67]:
df_all = pd.read_csv(path_all,sep="\t", header=None, comment='#')
df_all.columns = ['seqname' , 'source' , 'feature' , 'start' , 'end' , 'score' , 'strand' , 'frame' , 'attribute']
print(len(df_all.index))
total = df_all.index

150911


In [77]:
df_all = df_all[df_all.seqname != 'ChrUn']
print(len(df_all.index))


143137


In [78]:
#load genomic coordinates
df_genome = pd.read_csv(path_gff_genome,sep="\t", header=None)
df_genome.columns = ['seqname' , 'source' , 'feature' , 'start' , 'end' , 'score' , 'strand' , 'frame' , 'attribute']
g_ends = {}
for k,v in df_genome.iterrows():
    g_ends[v.seqname] = v.end

In [79]:
df_ann_te_chr = {}
for chromosome in df_ann_te.Chromosome.unique():
    df_ann_te_chr[chromosome] = df_ann_te[df_ann_te.Chromosome == chromosome]

In [ ]:
#overlapping
#merge DATs genes with DAT clusters
span = 0
current = 0
for k_g,v_g in df_all.iterrows():
    g_start = max(0, v_g.start - span)
    g_end = min(g_ends[v_g.seqname], v_g.end + span)
    g_strand = v_g.strand
    df_c = df_ann_te_chr[v_g.seqname]
    for k_s, v_s in df_c.iterrows():
        s_start = v_s.Start
        s_end = v_s.End
        if s_end >= g_start and s_start <= g_end:
            print(v_g.attribute, g_start, g_end, v_s['Repeat family'], s_start, s_end)
            current += 1
            break


LTR_id:4994;source_name:RLC_family136_LTR_7650_chr04_45985133_45988920;type:ltr;source:tephra;unique_id:7775 429 2347 rnd-6_family-1164 1207 1529
LTR_id:3831;source_name:RLG_LTR_63_FAM000516;type:ltr;source:TASR;unique_id:7776 20847 25597 rnd-5_family-183 22665 22915
LTR_id:6135;source_name:RLG_LTR_164_FAM001067;type:ltr;source:TASR;unique_id:7777 59855 61085 rnd-1_family-569 60711 61962
LTR_id:5770;source_name:RLG_LTR_259_FAM002147;type:ltr;source:TASR;unique_id:7778 70077 73078 rnd-1_family-1160 71807 72387
LTR_id:7116;source_name:RLG_LTR_472_FAM005410;type:ltr;source:TASR;unique_id:7779 73078 74106 rnd-1_family-717 73880 75047
LTR_id:2844;source_name:RLG_family114_LTR_13148_chr08_20618916_20625480;type:ltr;source:tephra;unique_id:7780 92606 95889 rnd-1_family-18 93329 94066
LTR_id:716;source_name:RLG_LTR_585_FAM007350;type:ltr;source:TASR;unique_id:7781 94659 95345 rnd-1_family-206 94441 95189
LTR_id:6737;source_name:RLG_LTR_93_FAM000751;type:ltr;source:TASR;unique_id:7782 111237 11

In [ ]:
print(total, current)